In [16]:
#### specify path of Julia Code for 2D Models ####
### By default the working directory ./2D_Models ###
path = string( pwd(), "/2D_Models/")

In [17]:
##### include 2D Modelling Framework ####
include(string(path, "./2D_model_library.jl"));


########## OPERATIONAL ##########
##### how to chose the actual velocity? #####

#op_model = "Constant"
#op_model = "Collision_Free_Speed"
#op_model = "RVO"
#op_model = "SocialForce"
#op_model = "AV_Model"
op_model = "AV_IN_Model"
#op_model = "IN_Costfunction"

#op_model = "Intrusion_Force"

include_op_model(op_model, path)

########## TACTICAL ##########
#### how to chose the preferred velocity? ###

tact_model = "Constant"
#tact_model = "IN_Model"

include_tact_model(tact_model, path)


########## STRATEGIC ##########
### how to chose the desired velocity ###

#strat_model = "Constant"
strat_model = "Towards_Goal"

include_strat_model(strat_model, path)


########## OPTIMIZATION SCHEME ##########
### If optimization of a cost-function is included, how to solve? ###

#optimization_scheme = "Regular_Sampling"
optimization_scheme = "Random_Sampling"

include_optimization_scheme(optimization_scheme, path)


##### which update scheme? #####

update = "Parallel_Update"
#update = "Step_Update"

include_update(update, path)


##### which order? i.e. Acceleration or Velocity based? ####
#order = "first"
order = "second"

include_order(order, path);

In [18]:
#### parameters of the agents ####
p = [1.7, 1.4, 2.0, 1.0, 0.4, 0.0, 0.0, 0.1, 0.02, 0.0, 0.0, 0.0, 0.6283185307179586]
# ModelParameter: v_max, v_des, T, T2, l, step_time, τ_A, τ_R, α, ζ_h, ζ_v, r, ϕ
p_desc = "v_max, T, T2, l, step_time, τ_A, τ_R, α, ζ_h, ζ_v, r, ϕ"

### of the system ###
N1 = 30
Δx = 2
N = Int(round(4*N1))
l1, l2 = Δx*N1, 4.0

system_size = (2.0*l1+l2, 2.0*l1+l2) #important for periodic boundaries

### of the simulation ###
sim_p = [0.0, 30.0, 0.05, 0.01, p[1]*p[3]] 
sim_p_desc = "t_relax, t_max, dt_save, dt, r"

### initialize geometry ###
geometrie = Create_Cross_Section(l1, l2, 0.1)

### initialize crowd ###
menge = create_crowd(N, geometrie)

Init_Hom_Parameters!(p, menge)
Init_Hom_Vels!(menge, 1.0)

d_goal = 10.0
Init_CrossSection_Crowds!(menge, geometrie, l1, l2 ,system_size, d_goal)

In [19]:
positions, headings = Simulate!(menge, geometrie, sim_p[1], sim_p[2], sim_p[3], sim_p[4], sim_p[5], system_size);

In [21]:
using GR
GR.inline("mov")

j = 1

dt_save = sim_p[3]
geometry_x, geometry_y = rewrite_geometry(geometrie)
boundaries_x, boundaries_y = boundaries_rectangle_positions(system_size)

#to set correct viewport
l_vp = 9
p1 = l1+l2/2-l_vp/2
p2 = l1+l2/2+l_vp/2

while j*sim_p[3] < sim_p[2]-sim_p[1]
    
        GR.clearws()
    
        GR.setwindow(p1, p2, p1, p2)
        GR.setviewport(0.0, 1, 0.0, 1)

        plot_geometry(geometry_x, geometry_y, 1.0, 20)
        
        #plot cross_section
        N = length(menge.agent)
        ΔN = Int(round(N/4))
    
        plot_agents(positions[j, 1:ΔN], headings[j, 1:ΔN], 2.3, 100, 0.7, 999, 0.1)
        plot_agents(positions[j, ΔN+1:2*ΔN], headings[j, ΔN+1:2*ΔN], 2.3, 96, 0.7, 999, 0.1)
        plot_agents(positions[j, 2*ΔN+1:3*ΔN], headings[j, 2*ΔN+1:3*ΔN], 2.3, 92, 0.7, 999, 0.1)
        plot_agents(positions[j, 3*ΔN+1:end], headings[j, 3*ΔN+1:end], 2.3, 88, 0.7, 999, 0.1)
  
        model = "AV*IN-model"
        timer = string("time ", round(j*dt_save, digits = 1), "s")
        GR.text(0.8, 0.95, timer)
        GR.text(0.8, 0.9, model)
        
        GR.updatews()
    
        j = j+1
end

In [22]:
GR.show()

GR.HTML("<video autoplay controls><source type=\"video/mp4\" src=\"data:video/mp4;base64,AAAAFGZ0eXBxdCAgAAACAHF0ICAAAAAId2lkZQA2hBBtZGF0AAACsQYF//+t3EXpvebZSLeWLNgg2SPu73gyNjQgLSBjb3JlIDE2MyAtIEguMjY0L01QRUctNCBBVkMgY29kZWMgLSBDb3B5bGVmdCAyMDAzLTIwMjEgLSBodHRwOi8vd3d3LnZpZGVvbGFuLm9yZy94MjY0Lmh0bWwgLSBvcHRpb25zOiBjYWJhYz0xIHJlZj0zIGRlYmxvY2s9MTowOjAgYW5hbHlzZT0weDM6MHgxMTMgbWU9aGV4IHN1Ym1lPTcgcHN5PTEgcHN5X3JkPTEuMDA6MC4wMCBtaXhlZF9yZWY9MSBtZV9yYW5nZT0xNiBjaHJvbWFfbWU9MSB0cmVsbGlzPTEgOHg4ZGN0PTEgY3FtPTAgZGVhZHpvbmU9MjEsMTEgZmFzdF9wc2tpcD0xIGNocm9tYV9xcF9vZmZzZXQ9LTIgdGhyZWFkcz0xMiBsb29rYWhlYWRfdGhyZWFkcz0yIHNsaWNlZF90aHJlYWRzPTAgbnI9MCBkZWNpbWF0ZT0xIGludGVybGFjZWQ9MCBibHVyYXlfY29tcGF0PTAgY29uc3RyYWluZWRfaW50cmE9MCBiZnJhbWVzPTMgYl9weXJhbWlkPTIgYl9hZGFwdD0xIGJfYmlhcz0wIGRpcmVjdD0xIHdlaWdodGI9MSBvcGVuX2dvcD0wIHdlaWdodHA9MiBrZXlpbnQ9MjUwIGtleWludF9taW49MjQgc2NlbmVjdXQ9NDAgaW50cmFfcmVmcmVzaD0wIHJjX2xvb2thaGVhZD00MCByYz1hYnIgbWJ0cmVlPTEgYml0cmF0ZT00MDAwIHJhdGV0b2w9MS4wIHFjb21wPTAuNjAgcXBtaW49MCBxcG1heD02OSBxcHN0ZXA9NCBpcF9yYXRpbz0xLjQwIGFxPTE6MS4wMACAAABIMGWIhAAY//73ye/AputbW7W/k89I/Cy3PsLsPSx7bg8/3Y2spaICzbKg9Rdmz40bnzw+EwFQEL9xsiUr1RfESR5UCzw7dz/Yxh3phMkJa33MLVo4EaxU3DarKrch8dM2eORG3bWTrbEneeN+uBZy9Kw8oLVLJJRg/PFwdqPOKNbLAdlDAMUHfsnz73xCOdtAVkmGHs7r0gdXWpoyLFj5jgKnbkZPtNX4zYjEvfoXtZwCE+7ZAVamCaow/yqftKL9U1ovJgGQvsRNDayMg++ve+NU92nb/IjGdgs9yqh8vn2LaFZxAAADAAADABV2qDLm6afFJiMNbyZKiJDwE40zr/SlYSWd9czpDZlPGJprYLst65kNad02PcfSVZjMdiJ+DF4aIXW3YXeVfCPmbGjMnXRwTq48XCjpqSzygtUsklGD88XHdOV4RrZYDsoYBiPitefWyhCOdtAVkmGHgC+vQAerLErme5xnZdGZm6Kg0XtXxop1k3psumuNZqtzxTLaLEvjfKy+yYQ6Pucc16ZMxux32RETSk2iTo3tLNbFMAASqnD8T0BfqpqKOvNkvga3Ydumc1vHk4ImdDZTiQ8QSzygtUsklGD88XLo1+rxtuPvP9YqUvsNL18G0ISNoCskwwqi9hMTceTgiZ0NlOMqiCWeUFqlkkowfni56GWSUZ8I7z/WKlApytdPG7UCrrAP1EMOfVbt7a3uZe15ffRmPNWgGgcI9SDGqaVft+2CzontPiOGIvvSLqWTxFUkyp1GV2BILm9X9D/wAAEeIoebJfBJtPm/kp7x5OCJnQ2U42uM9rjTSmrbUOOgzeTffPFGtlgOyhgGG4Jdrp43agVdYB+ohhE0Uo/k62xJ3njfq5a4Z7XGmlNW2ocdBm8vIX6vG24+8/1ipNyai9fBtCEjaArJMMOD7LM7YHoufTikx23MBtdYw1tOeDSgMUuY2KhwdqAF3RZgquu80yXM/Kwhw0Jov4P2I4MTePF2FDbxCtZtZNxcKUoKuInXe7LYi4Vp1THR/bQm/76VIAp+eewAQ0VXwWz53q6tgq26VmulHkPDcZIUKPquA60OUuKwyDl00AFp81BWd+FY2eyOMX5erk94bjZrHs9CSuD8R/9XxawJnO/zthiB/DDorXfr9H/yIHmV7LRmxvK+D2Fjb429HbDS/W1sXpkm5yDcBZbrCUv5g5wRrs+jdHkBbYIAQBJRB1OnVHiWMUYjiCeKc1Akg5FoeI4da3qEfgLLzNqd32jRYJ4KJ5PJQZ/ArKkE34tRPuFRJzaeQne/EzXBjjk58N0KPF93k+oM1jIPgp51OWhWAXgWBXe7YrgdJA430dnMSc5IbjGR1FXxl1SRr9ucaAnY0VBFWUqlBAIzsSqN5RPV2DJXmL/+SM8X8YkCdBIMfvDkzIBB/Gb5oXivRPVGaU4kxkBNNcewUDH+2FXj66Q6Cr4+yM92u0lHDLGXdns/FvKX2My26+1MrX8F8zEDZp/mlawnPJRoQT+im2GK64uR5JXVc9MAXXS7muDXWqx+qN/ml45bV9n7akeTQbP0q/mxj9edHmnfnY3NdmoWaY7vhz233oZJEIa6OoplL1RSvfVVGvXdVtAfDZ7Nn46hs3ZokQHuWFzLOaZA5z09VUuGzp3FYo0NwuSPUIrbe8uT+iiukOgqXD59lb+kvoeu/MmfEkMhrgZQWPveDLeESllwryIqaxAgVeMcDUSLWOxg11RV62WebBL/7rzixkdC1N/45VkJxUqpTm648L/vsQfbKMqUt/gmeUMGG2EEPbYElxv/qQ9UhCQjyOtZdNqGU1itEvade/LuTnu6o+YcjAtA4p5XtsbuZjCTCvI557kRFCqDzSBbBH+Gzj9LjNlKaMSeDW79pdjlXLSdqdnfhDqunp/rN4uvhQCTi5Ez7ZRmW87tsnt5X650QgkqkplQNHWpxNei83z8S13htYOnq6cUv+Wd2IvEjL+L5qtsdOO3rr/sBdnHsbYaCEU1tSIbAoWddi8NvUFXyRIAjBgIXYXtFG8PEKnHlAssRGh2v0C/s6mfIbW2l2JhNOoeXgi3q5EXMHwrZs7PG1wJZVASG9dKhxz+X6QIasKM+Ed5/rFSZMxxdfBtCEjaArJMMOAmYvFqnjAC8//e7cstU11heANFBQlUBvBSxvPA9DHzNLPL84GALFD2a6LRF5zBEIXPoxQT3Wrt1rmJd26ZJHv847R1Fy9/+Np1JfINqzEBtBsLzGJCrpLgKQFsOffoDGeBdO2KWYdZzXAsepTe4HrMhEKY4t6gBXPX/m2Zu0SJbcHdSUvNIjRemp2n7xiWl0T66KJqspxU6Lptl/BIUbboYPJqyBiqAkN66VDjn8v0h2i9pbbj7z/WKkjg02/dI6EJG0BWSYYKjhJ4t6sc+dmCOdFy2qz2JW57mph4Z7HVoDpw4ShuWsDkPBgYjCH7GGVqNbBEUMdHF0Id233/m7QBYY+waad47rJuHFuPZSGLPapw1h4r/TwoO9ViI///h/P53/6kpyxhfYlohPmD096bI1Qu+o6LdBnXVQGFZCux9yJZYRpKL97N53lxwjkAB7u8RqZKzK6wrYcYxDUu/uob7cFEiTSiSlozCAZ/bvMdG2qY4mtxlRdN8031zfDMhtLVpreod33Ja42pvD7omcjtcjM+IZAte1W3f8IaEuVQD4dxzsZMvRF4ry+t8f5w7DQraodtYaRiM7nIWmBeYkMT8+TZaHEqK9aCogIGgJ9VPlU6kukqtddNsrxOgHdMWFnfl02Wr7KcoYLuZAHbfU5poN0b5nzAjvDbSoYvUY9hYNtyqm30jI+K8RyV8px17f7CwD+HxjKzdhe0UbxDXjG0DVd6XRB4EO8QwgVENudGLWlE1aWfXSxmUi41wUBGspGHjerWCPS8GjXUOOfzAIs8JRRnwjvP9YqMNSK

In [5]:
Path = "/home/jakob/Dokumente/Sim_Data/"
dir = "Cross_Low_IN"
header = Header(p, p_desc, sim_p, sim_p_desc, op_model, tact_model, order, update, N, system_size);

#Save_Data!(Path, dir, header, positions)

In [6]:
samples = 100

for i in 1:samples 
    
    if mod(i, 10) == 0
        println(i)
        Random.seed!()
    end

    ### initialize geometry ###
    geometrie = Create_Cross_Section(l1, l2, 0.1)

    ### initialize crowd ###
    menge = create_crowd(N, geometrie)

    Init_Hom_Parameters!(p, menge)
    Init_Hom_Vels!(menge, 1.0)

    Init_CrossSection_Crowds!(menge, geometrie, l1, l2 ,system_size, d_goal)
    
    positions, headings, ttcs = Simulate!(menge, geometrie, sim_p[1], sim_p[2], sim_p[3], sim_p[4], sim_p[5], system_size);
    Save_Data!(Path, dir, header, positions)
    
end

10
20
30
40
50
60
70
80
90
100


In [ ]:
name = "90_Cross_Low"
path = "/home/jakob/Dokumente/Renne_Software/UMANS_3/examples/agents/"

Δ = l1 + 0.5*l2 


#Set_Goal_from_E_des!(menge, (99.0, 0.0))
#Change_Coordinate_System_Agents!(menge, -1 .*(system_size./2))
Change_Coordinate_System_Agents!(menge, -1 .*(Δ, Δ))

Write_Agents_XML(menge, name, path)

In [ ]:
path = "/home/jakob/Dokumente/Renne_Software/UMANS_3/examples/"
policy = "Moussaid"
agents = "90_Cross_HIGH"

name = string(agents, policy)


Write_Scenario_XML(path, name, sim_p, system_size, policy, agents)